In [1]:
import sys
import os
import pandas as pd
from pathlib import Path
from datetime import datetime
import argparse
import psutil
import numpy as np
import logging
import numpy as np
import tensorflow as tf
import time
import glob
from tensorflow.python.framework import ops
import math
from dotenv import find_dotenv, load_dotenv
import ftplib
from matplotlib import pyplot as plt
from collections import Counter

from scipy.stats.stats import pearsonr

nb_dir = os.path.join(Path(os.getcwd()).parents[0], 'src', 'data')
if nb_dir not in sys.path:
    sys.path.insert(0, nb_dir)
print(sys.path)
import features_selection as fs
import make_dataset as md
import build_data as bd
import get_raw_data as grd

models_dir = os.path.join(Path(os.getcwd()).parents[0], 'src', 'models')
if models_dir not in sys.path:
    sys.path.insert(0, models_dir)
import nn_real as nn

load_dotenv(find_dotenv())

pd.options.display.max_columns = 500
pd.options.display.max_rows = 500
pd.set_option('io.hdf.default_format','table')

C:\Users\sandr\AppData\Local\conda\conda\envs\tensorflowenvironment\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


['C:\\Users\\sandr\\Documents\\GitHub\\MLMortgage\\src\\data', '', 'C:\\Users\\sandr\\AppData\\Local\\conda\\conda\\envs\\tensorflowenvironment\\python36.zip', 'C:\\Users\\sandr\\AppData\\Local\\conda\\conda\\envs\\tensorflowenvironment\\DLLs', 'C:\\Users\\sandr\\AppData\\Local\\conda\\conda\\envs\\tensorflowenvironment\\lib', 'C:\\Users\\sandr\\AppData\\Local\\conda\\conda\\envs\\tensorflowenvironment', 'C:\\Users\\sandr\\AppData\\Local\\conda\\conda\\envs\\tensorflowenvironment\\lib\\site-packages', 'C:\\Users\\sandr\\AppData\\Local\\conda\\conda\\envs\\tensorflowenvironment\\lib\\site-packages\\Mako-1.0.7-py3.6.egg', 'C:\\Users\\sandr\\AppData\\Local\\conda\\conda\\envs\\tensorflowenvironment\\lib\\site-packages\\win32', 'C:\\Users\\sandr\\AppData\\Local\\conda\\conda\\envs\\tensorflowenvironment\\lib\\site-packages\\win32\\lib', 'C:\\Users\\sandr\\AppData\\Local\\conda\\conda\\envs\\tensorflowenvironment\\lib\\site-packages\\Pythonwin', 'C:\\Users\\sandr\\AppData\\Local\\conda\\con

In [16]:
pd.options.display.max_columns = 500
pd.options.display.max_rows = 500

RAW_DIR = os.path.join(Path(os.getcwd()).parents[0], 'data', 'raw') 
PRO_DIR = os.path.join(Path(os.getcwd()).parents[0], 'data', 'processed')
RANDOM_SEED = 123  # Set the seed to get reproducable results.
DT_FLOAT = np.float32
NP_FLOAT = np.dtype('float32')

train_dir = 'chuncks_random_1th_train' #'chuncks_random_c1mill_slices' #'chuncks_random_c1millx2_train'
raw_dir = 'chunks_all_c100th'
valid_dir = '' # 'chuncks_random_c1millx2_valid'
test_dir = ''
train_period=[121,323] #[121,279] #[121, 143] 
valid_period=[324,329] #[280,285] #[144, 147] 
test_period=[330,342] #[286,304] #[148, 155]
batch_size=100000

print(RAW_DIR, PRO_DIR)

def get_files_dict(train_dir, valid_dir, test_dir):        
    ext = "*.h5"

    files_dict = {'train': glob.glob(os.path.join(PRO_DIR, train_dir, ext)), 
                  'valid': glob.glob(os.path.join(PRO_DIR, valid_dir, ext)), 
                  'test': glob.glob(os.path.join(PRO_DIR, test_dir, ext))}

    return files_dict

def architecture_settings(files_dict):
    architecture = {}    
    ok_inputs = True
    
    for key in files_dict.keys():
        total_records = 0
        for file in files_dict[key]:                                
            with pd.HDFStore(file) as dataset_file:
                if (ok_inputs): 
                    index_length = len(dataset_file.get_storer(key+'/features').attrs.data_columns)
                    architecture['n_input'] = dataset_file.get_storer(key+ '/features').ncols - index_length
                    architecture['n_classes'] = dataset_file.get_storer(key+'/labels').ncols - index_length
                    ok_inputs = False                
                total_records += dataset_file.get_storer(key + '/features').nrows
        architecture[key + '_num_examples'] = total_records                            
    
    architecture['total_num_examples'] = architecture['train_num_examples'] # 10000000
    return architecture

#To sum up the dataset per worker (assuming the same size of files per worker approximately):
files_dict = get_files_dict(train_dir, valid_dir, test_dir)
architecture = architecture_settings(files_dict)
print(architecture)

C:\Users\sandr\Documents\GitHub\MLMortgage\data\raw C:\Users\sandr\Documents\GitHub\MLMortgage\data\processed
{'n_input': 261, 'n_classes': 7, 'train_num_examples': 93219, 'valid_num_examples': 0, 'test_num_examples': 0, 'total_num_examples': 93219}


In [13]:
DATA = md.get_h5_data(PRO_DIR, architecture, train_dir, None, None, train_period=train_period, valid_period=None, test_period=None)

C:\Users\sandr\Documents\GitHub\MLMortgage\data\raw C:\Users\sandr\Documents\GitHub\MLMortgage\data\processed
{'n_input': 261, 'n_classes': 7, 'train_num_examples': 93219, 'valid_num_examples': 0, 'test_num_examples': 0, 'total_num_examples': 93219}
C:\Users\sandr\Documents\GitHub\MLMortgage\data\processed\chuncks_random_1th_train\temporalloandynmodifmrstaticitur_FTrans_3Lab_100th-train_.h5 ...to load
C:\Users\sandr\Documents\GitHub\MLMortgage\data\processed\chuncks_random_1th_train\temporalloandynmodifmrstaticitur_FTrans_3Lab_100th-train_.h5  loaded in RAM
MBA_DELINQUENCY_STATUS is found 7 7 7
{'MBA_DELINQUENCY_STATUS': [[84, 85, 86, 87, 88, 89, 90], ['MBA_DELINQUENCY_STATUS_0', 'MBA_DELINQUENCY_STATUS_3', 'MBA_DELINQUENCY_STATUS_6', 'MBA_DELINQUENCY_STATUS_9', 'MBA_DELINQUENCY_STATUS_C', 'MBA_DELINQUENCY_STATUS_F', 'MBA_DELINQUENCY_STATUS_R']]}
val 84
total_ex:  0 self._total_num_examples:  93219
class_weights [0. 0. 0. 0. 0. 0. 0.]
val 85
total_ex:  0 self._total_num_examples:  9321

In [3]:
print(DATA.train._dict[0]['nrows'])
print(len(DATA.train.features_list), DATA.train.features_list)
print(len(DATA.train.labels_list), DATA.train.labels_list)

93219
261 ['MBA_DAYS_DELINQUENT', 'MBA_DAYS_DELINQUENT_NAN', 'CURRENT_INTEREST_RATE', 'CURRENT_INTEREST_RATE_NAN', 'LOANAGE', 'LOANAGE_NAN', 'CURRENT_BALANCE', 'CURRENT_BALANCE_NAN', 'SCHEDULED_PRINCIPAL', 'SCHEDULED_PRINCIPAL_NAN', 'SCHEDULED_MONTHLY_PANDI', 'SCHEDULED_MONTHLY_PANDI_NAN', 'LLMA2_CURRENT_INTEREST_SPREAD', 'LLMA2_CURRENT_INTEREST_SPREAD_NAN', 'LLMA2_C_IN_LAST_12_MONTHS', 'LLMA2_30_IN_LAST_12_MONTHS', 'LLMA2_60_IN_LAST_12_MONTHS', 'LLMA2_90_IN_LAST_12_MONTHS', 'LLMA2_FC_IN_LAST_12_MONTHS', 'LLMA2_REO_IN_LAST_12_MONTHS', 'LLMA2_0_IN_LAST_12_MONTHS', 'LLMA2_HIST_LAST_12_MONTHS_MIS', 'NUM_MODIF', 'NUM_MODIF_NAN', 'P_RATE_TO_MOD', 'P_RATE_TO_MOD_NAN', 'MOD_RATE', 'MOD_RATE_NAN', 'DIF_RATE', 'DIF_RATE_NAN', 'P_MONTHLY_PAY', 'P_MONTHLY_PAY_NAN', 'MOD_MONTHLY_PAY', 'MOD_MONTHLY_PAY_NAN', 'DIF_MONTHLY_PAY', 'DIF_MONTHLY_PAY_NAN', 'CAPITALIZATION_AMT', 'CAPITALIZATION_AMT_NAN', 'MORTGAGE_RATE', 'MORTGAGE_RATE_NAN', 'FICO_SCORE_ORIGINATION', 'INITIAL_INTEREST_RATE', 'ORIGINAL_LTV'

In [4]:
df_chunk = pd.DataFrame(DATA.train._dict[0]['dataset_features'], columns=DATA.train.features_list)
df_chunk[:10]

MBA_DAYS_DELINQUENT  MBA_DAYS_DELINQUENT_NAN  CURRENT_INTEREST_RATE  \
0             3.455598                      0.0               0.920721   
1            -0.332281                      0.0               0.240090   
2             2.192971                      0.0               0.625225   
3            -0.332281                      0.0               1.007207   
4             3.455598                      0.0               0.407207   
5             2.192971                      0.0              -0.262613   
6             2.192971                      0.0              -0.404955   
7             3.455598                      0.0              -0.899549   
8             3.455598                      0.0               0.001802   
9             3.455598                      0.0              -0.300450   

   CURRENT_INTEREST_RATE_NAN   LOANAGE  LOANAGE_NAN  CURRENT_BALANCE  \
0                        0.0  1.822959          0.0        -0.266641   
1                        0.0  1.710194          0.0        -0.216199   
2                        0.0  0.853180          0.0        -0.138843   
3                        0.0  1.078710          0.0        -0.153359   
4                        0.0  1.304240          0.0        -0.663479   
5                        0.0  1.597429          0.0         0.019590   
6                        0.0  1.439558          0.0        -0.059639   
7                        0.0  3.221245          0.0        -0.390625   
8                        0.0  2.206360          0.0        -0.216933   
9                        0.0  1.078710          0.0        -0.662329   

   CURRENT_BALANCE_NAN  SCHEDULED_PRINCIPAL  SCHEDULED_PRINCIPAL_NAN  \
0                  0.0        -1.478814e-01                      0.0   
1                  0.0        -1.478814e-01                      0.0   
2                  0.0        -1.460663e-09                      1.0   
3                  0.0        -1.460663e-09                      1.0   
4                  0.0        -1.478814e-01                      0.0   
5                  0.0        -1.478814e-01                      0.0   
6                  0.0        -1.478814e-01                      0.0   
7                  0.0        -1.460663e-09                      1.0   
8                  0.0        -1.460663e-09                      1.0   
9                  0.0        -1.478814e-01                      0.0   

   SCHEDULED_MONTHLY_PANDI  SCHEDULED_MONTHLY_PANDI_NAN  \
0            -7.183462e-02                          0.0   
1            -4.447126e-02                          0.0   
2            -5.645501e-09                          1.0   
3            -5.645501e-09                          1.0   
4            -2.884292e-01                          0.0   
5            -1.595169e-02                          0.0   
6            -1.373525e-01                          0.0   
7            -2.150337e-01                          0.0   
8            -1.182097e-01                          0.0   
9            -3.057721e-01                          0.0   

   LLMA2_CURRENT_INTEREST_SPREAD  LLMA2_CURRENT_INTEREST_SPREAD_NAN  \
0                       0.059903                                0.0   
1                      -0.602416                                0.0   
2                      -0.793237                                0.0   
3                       0.200966                                0.0   
4                      -0.428019                                0.0   
5                      -0.412077                                0.0   
6                      -0.777295                                0.0   
7                      -0.877778                                0.0   
8                      -0.630918                                0.0   
9                      -0.843961                                0.0   

   LLMA2_C_IN_LAST_12_MONTHS  LLMA2_30_IN_LAST_12_MONTHS  \
0                  -1.909091                    1.708738   
1                  -2.161616                    2.

In [5]:
df_labels = pd.DataFrame(DATA.train._dict[0]['dataset_labels'])
y = df_labels.idxmax(axis=1)
display(y)
display(y.value_counts())
class_dict = {'0': 0, '3': 1, '6': 2, '9': 3, 'C': 4, 'F': 5, 'R': 6}
display(class_dict)

0        1
1        1
2        1
3        1
4        1
5        1
6        1
7        1
8        1
9        1
10       1
11       1
12       1
13       1
14       1
15       1
16       1
17       1
18       1
19       1
20       1
21       1
22       1
23       1
24       1
25       1
26       1
27       1
28       1
29       1
30       1
31       1
32       1
33       1
34       1
35       1
36       1
37       1
38       1
39       1
40       1
41       1
42       1
43       1
44       1
45       1
46       1
47       1
48       1
49       1
50       1
51       1
52       1
53       1
54       1
55       1
56       1
57       1
58       1
59       1
60       1
61       1
62       1
63       1
64       1
65       1
66       1
67       1
68       1
69       1
70       1
71       1
72       1
73       1
74       1
75       1
76       1
77       1
78       1
79       1
80       1
81       1
82       1
83       1
84       1
85       1
86       1
87       1
88       1
89       1
90       1

1    93219
dtype: int64

{'0': 0, '3': 1, '6': 2, '9': 3, 'C': 4, 'F': 5, 'R': 6}

In [ ]:
#df_sample = df_chunk.sample(frac=0.05, replace=False)
##df_sample = pd.DataFrame(subset, columns=ncols).sample(frac=0.05, replace=False)

In [ ]:
#print(df_sample.shape)
#display(df_sample[:10])

In [ ]:
#print(df_sample.index.values)
#y_sample = y.loc[df_sample.index.values]
#print(y_sample.shape)
#print(y_sample[:10])
#display(y_sample.value_counts())
#class_dict = {'0': 0, '3': 1, '6': 2, '9': 3, 'C': 4, 'F': 5, 'R': 6}
#display(class_dict)

In [ ]:
#import numpy as np
#from kmodes.kmodes import KModes

## random categorical data
#data = np.random.choice(20, (100, 10))

#print(data)

#km = KModes(n_clusters=4, init='Huang', n_init=5, verbose=1) #, n_jobs=-1

#print(km)

In [ ]:
#clusters = km.fit_predict(data)

## Print the cluster centroids
#print(km.cluster_centroids_)

In [ ]:
#print(clusters)

In [ ]:
from kmodes.kprototypes import KPrototypes
kp = KPrototypes(n_clusters=7, init='Huang', n_init=8, verbose=1) #, n_jobs=-1)

print(kp)

In [ ]:
#mixed_data = np.concatenate((np.random.choice(20, (100, 10)), (np.random.rand(100,5))), axis=1)

In [ ]:
#display(mixed_data.shape)
#display(mixed_data[0][9])
#cat_idxs = list(range(10))
#print(cat_idxs)

In [6]:
categorical_cols = {'MBA_DELINQUENCY_STATUS':  ['0','3','6','9','C','F','R'],
                       'BUYDOWN_FLAG': ['N','U','Y'], 'NEGATIVE_AMORTIZATION_FLAG': ['N','U','Y'], 'PREPAY_PENALTY_FLAG': ['N','U','Y'],
                       'OCCUPANCY_TYPE': ['1','2','3','U'], 'PRODUCT_TYPE': ['10','20','30','40','50','51','52','53','54','5A','5Z',
                                        '60','61','62','63','6Z','70','80','81','82','83','84','8Z','U'], 
                       'PROPERTY_TYPE': ['1','2','3','4','5','6','7','8','9','L','M','U','Z'], 'LOAN_PURPOSE_CATEGORY': ['P','R','U'], 
                       'DOCUMENTATION_TYPE': ['1','2','3','U'], 'CHANNEL': ['1','2','3','4','5','6','7','8','9','A','B','C','D','U'], 
                       'LOAN_TYPE': ['1','2','3','4','5','6','7','U'], 'IO_FLAG': ['N','U','Y'], 
                       'CONVERTIBLE_FLAG': ['N','U','Y'], 'POOL_INSURANCE_FLAG': ['N','U','Y'], 'STATE': ['AK', 'AL', 'AR', 'AZ', 'CA', 'CO',
                                           'CT', 'DC', 'DE', 'FL', 'GA', 'HI', 'IA', 'ID', 'IL', 'IN', 'KS', 'KY', 'LA', 'MA', 
                                           'MD', 'ME', 'MI', 'MN', 'MO', 'MS', 'MT', 'NC', 'ND', 'NE', 'NH', 'NJ', 'NM', 'NV', 
                                           'NY', 'OH', 'OK', 'OR', 'PA', 'PR', 'RI', 'SC', 'SD', 'TN', 'TX', 'UT', 'VA', 'VT', 
                                           'WA', 'WI', 'WV', 'WY'], 
                       'CURRENT_INVESTOR_CODE': ['240', '250', '253', 'U'], 'ORIGINATION_YEAR': ['B1995','1995','1996','1997','1998','1999','2000','2001','2002','2003',
                                                '2004','2005','2006','2007','2008','2009','2010','2011','2012','2013','2014','2015','2016','2017','2018','nan']}
idx_categorical_cols = {}

for cat, values in categorical_cols.items():
    idx_categorical_cols[cat] = [[], []]
    if any(cat in s for s in DATA.train.features_list):        
        idx_categorical_cols[cat][0].extend([DATA.train.features_list.index(cat+'_'+v) for v in values])
        idx_categorical_cols[cat][1].extend([cat+'_'+v for v in values])
        print(cat, 'is found', len(values), len(idx_categorical_cols[cat][0]), len(idx_categorical_cols[cat][1]))
display(idx_categorical_cols)

MBA_DELINQUENCY_STATUS is found 7 7 7
BUYDOWN_FLAG is found 3 3 3
NEGATIVE_AMORTIZATION_FLAG is found 3 3 3
PREPAY_PENALTY_FLAG is found 3 3 3
OCCUPANCY_TYPE is found 4 4 4
PRODUCT_TYPE is found 24 24 24
PROPERTY_TYPE is found 13 13 13
LOAN_PURPOSE_CATEGORY is found 3 3 3
DOCUMENTATION_TYPE is found 4 4 4
CHANNEL is found 14 14 14
LOAN_TYPE is found 8 8 8
IO_FLAG is found 3 3 3
CONVERTIBLE_FLAG is found 3 3 3
POOL_INSURANCE_FLAG is found 3 3 3
STATE is found 52 52 52
CURRENT_INVESTOR_CODE is found 4 4 4
ORIGINATION_YEAR is found 26 26 26


{'BUYDOWN_FLAG': [[91, 92, 93],
  ['BUYDOWN_FLAG_N', 'BUYDOWN_FLAG_U', 'BUYDOWN_FLAG_Y']],
 'CHANNEL': [[148,
   149,
   150,
   151,
   152,
   153,
   154,
   155,
   156,
   157,
   158,
   159,
   160,
   161],
  ['CHANNEL_1',
   'CHANNEL_2',
   'CHANNEL_3',
   'CHANNEL_4',
   'CHANNEL_5',
   'CHANNEL_6',
   'CHANNEL_7',
   'CHANNEL_8',
   'CHANNEL_9',
   'CHANNEL_A',
   'CHANNEL_B',
   'CHANNEL_C',
   'CHANNEL_D',
   'CHANNEL_U']],
 'CONVERTIBLE_FLAG': [[173, 174, 175],
  ['CONVERTIBLE_FLAG_N', 'CONVERTIBLE_FLAG_U', 'CONVERTIBLE_FLAG_Y']],
 'CURRENT_INVESTOR_CODE': [[231, 232, 233, 234],
  ['CURRENT_INVESTOR_CODE_240',
   'CURRENT_INVESTOR_CODE_250',
   'CURRENT_INVESTOR_CODE_253',
   'CURRENT_INVESTOR_CODE_U']],
 'DOCUMENTATION_TYPE': [[144, 145, 146, 147],
  ['DOCUMENTATION_TYPE_1',
   'DOCUMENTATION_TYPE_2',
   'DOCUMENTATION_TYPE_3',
   'DOCUMENTATION_TYPE_U']],
 'IO_FLAG': [[170, 171, 172], ['IO_FLAG_N', 'IO_FLAG_U', 'IO_FLAG_Y']],
 'LOAN_PURPOSE_CATEGORY': [[141, 142, 143],


In [10]:
df_sample_scat = df_chunk.copy() # df_sample.copy()
for cat, values in idx_categorical_cols.items():
    cat_cols = [elem for elem in values[1]]
    cat_subset = df_sample_scat[cat_cols]
    cat_subset.columns = range(0,len(cat_cols))
    assert(cat_subset.sum(axis=1).all() == 1)
    cat_sc = cat_subset.idxmax(axis=1)
    cat_sc.name = cat    
    display(cat_sc.value_counts().shape, cat_sc.value_counts())
    df_sample_scat.drop(cat_cols, axis=1, inplace=True)
    df_sample_scat[cat] = cat_sc

(1,)

5    93219
Name: MBA_DELINQUENCY_STATUS, dtype: int64

(3,)

0    67336
1    24854
2     1029
Name: BUYDOWN_FLAG, dtype: int64

(3,)

...

4     11076
44     8368
9      7086
10     4670
14     4086
34     4084
22     3849
35     3324
38     3203
27     2924
31     2568
20     2489
46     2310
15     2211
3      2203
48     1956
24     1955
5      1831
23     1816
19     1770
43     1624
41     1438
18     1268
1      1252
6      1089
33      973
49      971
45      926
36      916
37      847
17      843
25      722
16      674
12      649
32      610
50      534
2       447
30      441
29      415
13      389
8       386
40      364
21      285
11      273
7       264
26      200
42      149
28      117
47      114
51       92
0        92
39       76
Name: STATE, dtype: int64

(4,)

3    60815
2    26617
0     3482
1     2305
Name: CURRENT_INVESTOR_CODE, dtype: int64

(21,)

11    10156
12     9669
10     8518
9      8228
0      7910
13     6889
5      6615
8      6174
4      5877
7      5055
6      4186
3      3762
2      2934
1      2382
14     2335
15     1214
16      655
17      376
18      207
19       66
20       11
Name: ORIGINATION_YEAR, dtype: int64

In [11]:
display(df_sample_scat.shape, df_sample_scat) #[:10]

(93219, 101)

MBA_DAYS_DELINQUENT  MBA_DAYS_DELINQUENT_NAN  CURRENT_INTEREST_RATE  \
0                 3.455598                      0.0               0.920721   
1                -0.332281                      0.0               0.240090   
2                 2.192971                      0.0               0.625225   
3                -0.332281                      0.0               1.007207   
4                 3.455598                      0.0               0.407207   
5                 2.192971                      0.0              -0.262613   
6                 2.192971                      0.0              -0.404955   
7                 3.455598                      0.0              -0.899549   
8                 3.455598                      0.0               0.001802   
9                 3.455598                      0.0              -0.300450   
10                1.561658                      0.0               0.917117   
11                2.192971                      0.0              -0.521171   
12                1.561658                      0.0               0.868469   
13               -0.332281                      0.0               1.022072   
14                1.561658                      0.0               0.869820   
15                1.561658                      0.0               1.033333   
16                0.299032                      0.0               0.647748   
17                0.930345                      0.0               0.463964   
18                2.192971                      0.0               0.999550   
19                2.192971                      0.0              -0.252703   
20                1.561658                      0.0               0.858108   
21                2.192971                      0.0               3.752252   
22                0.299032                      0.0               2.855856   
23                0.930345                      0.0               2.229730   
24                0.930345                      0.0               2.756757   
25                0.930345                      0.0               2.756757   
26                0.299032                      0.0               1.806306   
27                0.299032                      0.0               3.481982   
28                0.930345                      0.0               3.954955   
29                2.192971                      0.0               1.702703   
30                0.930345                      0.0               2.716216   
31                0.299032                      0.0               3.617117   
32                0.930345                      0.0               3.324324   
33                0.930345                      0.0               2.324324   
34                0.930345                      0.0               3.549550   
35                0.299032                      0.0               1.027027   
36                2.192971                      0.0               3.756757   
37                1.561658                      0.0               3.977478   
38                1.561658                      0.0               3.162162   
39                0.930345                      0.0               3.954955   
40                2.192971                      0.0               1.810811   
41                2.192971                      0.0               3.504504   
42                0.930345                      0.0               3.471622   
43                2.192971                      0.0               1.869369   
44                0.299032                      0.0               2.815315   
45                1.561658                      0.0               1.423424   
46                2.192971                      0.0               2.792793   
47                1.561658                      0.0               1.702703   
48                2.192971                      0.0               3.887388   
49               -0.332281                      0.0               2.445946   
50                0.930345   

In [ ]:
### Original dataset:

In [17]:
all_files = glob.glob(os.path.join(RAW_DIR, raw_dir, '*.txt'))
print(all_files)

['C:\\Users\\sandr\\Documents\\GitHub\\MLMortgage\\data\\raw\\chunks_all_c100th\\temporalloandynmodifmrstaticitur_FTrans_3Lab_100th.txt']


In [18]:
original_data = pd.read_csv(all_files[0], sep=',', low_memory=False)

In [19]:
original_data

Loan_Id  Period   AsOfMonth MBA_Delinquency_Status  \
0         1185110     150  2001-07-01                      F   
1         1209182     159  2002-04-01                      F   
2         1241195     134  2000-03-01                      F   
3         1241195     144  2001-01-01                      F   
4         1245745     156  2002-01-01                      F   
5         1251549     172  2003-05-01                      F   
6         1259067     168  2003-01-01                      F   
7         1267854     252  2010-01-01                      F   
8         1277835     211  2006-08-01                      F   
9         1282745     163  2002-08-01                      F   
10        1305120     143  2000-12-01                      F   
11        1323687     178  2003-11-01                      F   
12        1327723     150  2001-07-01                      F   
13        1376455     145  2001-02-01                      F   
14        1388434     136  2000-05-01                      F   
15        1395429     148  2001-05-01                      F   
16        1417383     132  2000-01-01                      F   
17        1418989     137  2000-06-01                      F   
18        1420917     145  2001-02-01                      F   
19        1424964     168  2003-01-01                      F   
20        1449308     126  1999-07-01                      F   
21        2108228     156  2002-01-01                      F   
22        2109380     136  2000-05-01                      F   
23        2112785     181  2004-02-01                      F   
24        2142353     132  2000-01-01                      F   
25        2142353     134  2000-03-01                      F   
26        2169654     129  1999-10-01                      F   
27        2182221     139  2000-08-01                      F   
28        2189581     135  2000-04-01                      F   
29        2192494     154  2001-11-01                      F   
30        2281560     127  1999-08-01                      F   
31        2284758     139  2000-08-01                      F   
32        2290442     127  1999-08-01                      F   
33        2307687     131  1999-12-01                      F   
34        2334880     127  1999-08-01                      F   
35        2354631     139  2000-08-01                      F   
36        2356194     152  2001-09-01                      F   
37        2356486     129  1999-10-01                      F   
38        2356554     218  2007-03-01                      F   
39        2362500     127  1999-08-01                      F   
40        2394662     160  2002-05-01                      F   
41        2395531     169  2003-02-01                      F   
42        2419416     175  2003-08-01                      F   
43        2442168     143  2000-12-01                      F   
44        2450449     139  2000-08-01                      F   
45        2458584     129  1999-10-01                      F   
46        2502868     185  2004-06-01                      F   
47        2518855     186  2004-07-01                      F   
48        2543262     152  2001-09-01                      F   
49        2572325     264  2011-01-01                      F   
50        2600702     133  2000-02-01                      F   
51        2624155     129  1999-10-01                      F   
52        2625448     134  2000-03-01                      F   
53        2625448     139  2000-08-01                      F   
54        2627018     133  2000-02-01                      F   
55        2632912     131  1999-12-01                      F   
56        2658301     197  2005-06-01                      F   
57        2685778     182  2004-03-01                      F   
58        2688091     149  2001-06-01                      F   
59        2701120     148  2001-05-01                      F   
60        2710588     168  2003-01-01                      F   
61        2717485     139  2000-08-01     

In [21]:
for column in original_data[3:]: 
    display(original_data[column].value_counts())


111946606     6
112079499     6
115665288     5
111613668     5
131121064     5
129152133     5
111706143     5
113224479     4
128058498     4
111384563     4
116526086     4
26063048      4
125615858     4
111180655     4
111535374     4
25276006      4
128116712     4
136978128     4
1142578092    4
1122760003    4
28918873      4
111525856     4
26748572      4
128978703     4
125556857     4
137585034     4
1141869707    4
1203265       4
127719421     4
115325746     4
136528913     4
127471681     4
112240948     4
1118377481    4
145356191     4
1126748051    4
136536874     4
111579214     3
111506874     3
1160772210    3
226274136     3
115950423     3
1177714204    3
1367717       3
111226652     3
14150704      3
1118329765    3
225490660     3
128194714     3
128686387     3
225818720     3
19962110      3
224729301     3
21396314      3
27355827      3
226161473     3
127396775     3
116294523     3
116734794     3
1467394       3
138388589     3
27019697      3
12870781

267    852
234    845
254    818
238    775
159    760
237    750
297    731
219    706
171    701
148    695
268    687
266    675
170    674
162    674
239    664
172    663
163    659
158    649
218    637
255    635
160    635
269    633
279    627
232    627
161    620
256    618
207    614
264    613
272    610
265    607
156    606
166    605
168    605
258    604
235    604
195    600
221    596
220    594
228    587
165    586
280    585
173    583
275    579
194    576
167    572
183    570
233    568
231    567
147    566
217    564
285    564
262    563
216    563
164    563
271    561
177    560
252    555
182    554
185    552
257    551
215    548
178    547
169    544
149    543
263    543
190    538
229    535
273    534
230    533
236    532
270    530
214    530
184    520
154    518
281    517
150    517
291    516
276    516
179    515
259    515
157    508
278    504
286    503
261    502
212    499
274    499
206    498
227    498
213    492
260    489
146    487

2011-04-01    852
2008-07-01    845
2010-03-01    818
2008-11-01    775
2002-04-01    760
2008-10-01    750
2013-10-01    731
2007-04-01    706
2003-04-01    701
2001-05-01    695
2011-05-01    687
2011-03-01    675
2003-03-01    674
2002-07-01    674
2008-12-01    664
2003-05-01    663
2002-08-01    659
2002-03-01    649
2007-03-01    637
2002-05-01    635
2010-04-01    635
2011-06-01    633
2012-04-01    627
2008-05-01    627
2002-06-01    620
2010-05-01    618
2006-04-01    614
2011-01-01    613
2011-09-01    610
2011-02-01    607
2002-01-01    606
2002-11-01    605
2003-01-01    605
2008-08-01    604
2010-07-01    604
2005-04-01    600
2007-06-01    596
2007-05-01    594
2008-01-01    587
2002-10-01    586
2012-05-01    585
2003-06-01    583
2011-12-01    579
2005-03-01    576
2002-12-01    572
2004-04-01    570
2008-06-01    568
2008-04-01    567
2001-04-01    566
2012-10-01    564
2007-02-01    564
2002-09-01    563
2010-11-01    563
2007-01-01    563
2011-08-01    561
2003-10-01

F    100000
Name: MBA_Delinquency_Status, dtype: int64

180.0    32041
0.0      19606
150.0    14714
120.0    13656
90.0      9144
60.0      5637
30.0      5147
Name: MBA_Days_Delinquent, dtype: int64

...

0    99991
1        9
Name: LLMA2_ORIG_RATE_ORIG_MR_SPREAD_nan, dtype: int64

0    80108
1    19104
2      701
3       69
4       17
7        1
Name: count_int_rate_less, dtype: int64

15581.0    91
16767.0    91
16426.0    91
5189.0     85
23103.0    85
11482.0    82
29102.0    81
17082.0    77
12434.0    72
13543.0    70
14906.0    70
16358.0    69
12128.0    68
7078.0     67
11012.0    67
21165.0    67
12808.0    66
26594.0    65
12472.0    65
14793.0    65
7030.0     64
14064.0    63
13984.0    62
23938.0    62
39994.0    62
7101.0     61
16433.0    61
7056.0     60
11718.0    60
4735.0     58
24855.0    58
26608.0    58
11037.0    57
22803.0    57
7065.0     57
6057.0     57
6947.0     57
22316.0    57
7684.0     57
11662.0    56
11481.0    56
10936.0    56
12142.0    55
22304.0    55
31463.0    55
4600.0     55
8412.0     54
6906.0     54
5846.0     53
9581.0     53
22669.0    52
25397.0    52
12658.0    51
9514.0     51
14687.0    51
6841.0     50
9732.0     50
18259.0    50
5749.0     50
3722.0     50
5810.0     49
11021.0    49
19242.0    49
5004.0     49
9368.0     49
6499.0     49
17518.0    48
20334.0    48
9038.0     48
27403.0    48
30769.0    47
34035.

0    99989
1       11
Name: num_prime_zip_nan, dtype: int64

1    100000
Name: consecutive, dtype: int64

In [22]:
original_data['count_int_rate_less'].value_counts()

0    80108
1    19104
2      701
3       69
4       17
7        1
Name: count_int_rate_less, dtype: int64

In [23]:
original_data['Loan_Id'].value_counts()

111946606     6
112079499     6
115665288     5
111613668     5
131121064     5
129152133     5
111706143     5
113224479     4
128058498     4
111384563     4
116526086     4
26063048      4
125615858     4
111180655     4
111535374     4
25276006      4
128116712     4
136978128     4
1142578092    4
1122760003    4
28918873      4
111525856     4
26748572      4
128978703     4
125556857     4
137585034     4
1141869707    4
1203265       4
127719421     4
115325746     4
136528913     4
127471681     4
112240948     4
1118377481    4
145356191     4
1126748051    4
136536874     4
111579214     3
111506874     3
1160772210    3
226274136     3
115950423     3
1177714204    3
1367717       3
111226652     3
14150704      3
1118329765    3
225490660     3
128194714     3
128686387     3
225818720     3
19962110      3
224729301     3
21396314      3
27355827      3
226161473     3
127396775     3
116294523     3
116734794     3
1467394       3
138388589     3
27019697      3
12870781

In [25]:
original_data[original_data['count_int_rate_less']==7]


Loan_Id  Period   AsOfMonth MBA_Delinquency_Status  \
38156  13689201     173  2003-06-01                      F   

       MBA_Days_Delinquent  MBA_DAYS_DELINQUENT_nan  Current_Interest_Rate  \
38156                180.0                        0                  4.407   

       CURRENT_INTEREST_RATE_nan  Loanage  Loanage_nan  Current_Balance  \
38156                          0      176            0         140917.0   

       current_balance_nan  Scheduled_Principal  SCHEDULED_PRINCIPAL_nan  \
38156                    0                  0.0                        0   

       Scheduled_Monthly_PandI  SCHEDULED_MONTHLY_PANDI_nan  \
38156                   1065.0                            0   

      Current_Investor_Code  year  month  LLMA2_CURRENT_INTEREST_SPREAD  \
38156                   U    2003      6                         -0.823   

       LLMA2_CURRENT_INTEREST_SPREAD_nan  LLMA2_C_IN_LAST_12_MONTHS  \
38156                                  0                        0.0   

       LLMA2_30_IN_LAST_12_MONTHS  LLMA2_60_IN_LAST_12_MONTHS  \
38156                         2.0                         2.0   

       LLMA2_90_IN_LAST_12_MONTHS  LLMA2_FC_IN_LAST_12_MONTHS  \
38156                         2.0                         6.0   

       LLMA2_REO_IN_LAST_12_MONTHS  LLMA2_0_IN_LAST_12_MONTHS  \
38156                          0.0                        0.0   

       LLMA2_HIST_LAST_12_MONTHS_MIS  Period_next  Delinquency_Status_next  \
38156                              0          NaN                        3   

       Invalid_transitions  Num_Modif  Num_Modif_nan  mod_per_from  \
38156                    0        NaN              1           NaN   

       mod_per_to  P_Rate_to_Mod  P_Rate_to_Mod_nan  Mod_Rate  Mod_Rate_nan  \
38156         NaN            NaN                  1       NaN             1   

       dif_rate  dif_rate_nan  P_Monthly_Pay  P_Monthly_Pay_nan  \
38156       NaN             1            NaN                  1   

       Mod_Monthly_Pay  Mod_Monthly_Pay_nan  dif_monthly_pay  \
38156              NaN                    1              NaN   

       dif_monthly_pay_nan  Capitalization_Amt  Capitalization_Amt_nan  \
38156                    1                 NaN                       1   

       Mortgage_Rate  Mortgage_Rate_nan  FICO_Score_Origination  \
38156           5.23                  0                     585   

       Initial_Interest_Rate  Original_LTV  Original_Balance  BackEnd_Ratio  \
38156                  7.294         74.96          184800.0            NaN   

       BACKEND_RATIO_nan  Original_Term  ORIGINAL_TERM_nan  Sale_Price  \
38156                  1          360.0                  0    246500.0   

       SALE_PRICE_nan Buydown_Flag Negative_Amortization_Flag  \
38156               0            N                          Y   

      Prepay_Penalty_Flag  Prepay_Penalty_Term  PREPAY_PENALTY_TERM_nan  \
38156                   U                  NaN                        1   

      Occupancy_Type Product_Type Property_Type Loan_Purpose_Category  \
38156              1           20             1                     P   

      Documentation_Type Channel Loan_Type  Number_of_Units  \
38156                  1       1         1              1.0   

       NUMBER_OF_UNITS_nan IO_Flag  Margin  MARGIN_nan  Periodic_Rate_Cap  \
38156                    0       U    2.15           0              9.999   

       PERIODIC_RATE_CAP_nan  Periodic_Rate_Floor  PERIODIC_RATE_FLOOR_nan  \
38156                      0                  0.0                        0   

       Lifetime_Rate_Cap  LIFETIME_RATE_CAP_nan  Lifetime_Rate_Floor  \
38156              13.15                      0                 2.15   

       LIFETIME_RATE_FLOOR_nan  Rate_Reset_Frequency  \
38156                        0                   1.0   

       RATE_RESET_FREQUENCY_nan  Pay_Reset_Frequency  PAY_RESET_FREQUENCY_nan  \
38156                         0                 12.0                        0   

      

In [26]:
original_data[original_data['Loan_Id']==13689201]

Loan_Id  Period   AsOfMonth MBA_Delinquency_Status  \
38154  13689201     130  1999-11-01                      F   
38155  13689201     155  2001-12-01                      F   
38156  13689201     173  2003-06-01                      F   

       MBA_Days_Delinquent  MBA_DAYS_DELINQUENT_nan  Current_Interest_Rate  \
38154                180.0                        0                  6.650   
38155                180.0                        0                  6.256   
38156                180.0                        0                  4.407   

       CURRENT_INTEREST_RATE_nan  Loanage  Loanage_nan  Current_Balance  \
38154                          0      133            0         158639.0   
38155                          0      158            0         150184.0   
38156                          0      176            0         140917.0   

       current_balance_nan  Scheduled_Principal  SCHEDULED_PRINCIPAL_nan  \
38154                    0                  NaN                        1   
38155                    0                  0.0                        0   
38156                    0                  0.0                        0   

       Scheduled_Monthly_PandI  SCHEDULED_MONTHLY_PANDI_nan  \
38154                      NaN                            1   
38155                   1296.0                            0   
38156                   1065.0                            0   

      Current_Investor_Code  year  month  LLMA2_CURRENT_INTEREST_SPREAD  \
38154                   U    1999     11                         -1.087   
38155                   U    2001     12                         -0.814   
38156                   U    2003      6                         -0.823   

       LLMA2_CURRENT_INTEREST_SPREAD_nan  LLMA2_C_IN_LAST_12_MONTHS  \
38154                                  0                        1.0   
38155                                  0                        0.0   
38156                                  0                        0.0   

       LLMA2_30_IN_LAST_12_MONTHS  LLMA2_60_IN_LAST_12_MONTHS  \
38154                         4.0                         2.0   
38155                         2.0                         3.0   
38156                         2.0                         2.0   

       LLMA2_90_IN_LAST_12_MONTHS  LLMA2_FC_IN_LAST_12_MONTHS  \
38154                         1.0                         4.0   
38155                         0.0                         7.0   
38156                         2.0                         6.0   

       LLMA2_REO_IN_LAST_12_MONTHS  LLMA2_0_IN_LAST_12_MONTHS  \
38154                          0.0                        0.0   
38155                          0.0                        0.0   
38156                          0.0                        0.0   

       LLMA2_HIST_LAST_12_MONTHS_MIS  Period_next  Delinquency_Status_next  \
38154                              0        136.0                        3   
38155                              0        161.0                        3   
38156                              0          NaN                        3   

       Invalid_transitions  Num_Modif  Num_Modif_nan  mod_per_from  \
38154                    0        NaN              1           NaN   
38155                    0        NaN              1           NaN   
38156                    0        NaN              1           NaN   

       mod_per_to  P_Rate_to_Mod  P_Rate_to_Mod_nan  Mod_Rate  Mod_Rate_nan  \
38154         NaN            NaN                  1       NaN             1   
38155         NaN            NaN                  1       NaN             1   
38156         NaN            NaN                  1       NaN             1   

       dif_rate  dif_rate_nan  P_Monthly_Pay  P_Monthly_Pay_nan  \
38154       NaN             1            NaN                  1   
38155       NaN             1            NaN                  1   
38156       NaN             1            NaN                  1   

       Mod_Monthly_Pay  Mod_Monthly_Pa

In [ ]:
cat_idxs = list(range(df_sample_scat.columns.get_loc('MBA_DELINQUENCY_STATUS'), 101))
cat_idxs

In [ ]:
numeric_cols = ['MBA_DAYS_DELINQUENT', 'MBA_DAYS_DELINQUENT_NAN',
   'CURRENT_INTEREST_RATE', 'CURRENT_INTEREST_RATE_NAN', 'LOANAGE', 'LOANAGE_NAN',
   'CURRENT_BALANCE', 'CURRENT_BALANCE_NAN', 'SCHEDULED_PRINCIPAL',
   'SCHEDULED_PRINCIPAL_NAN', 'SCHEDULED_MONTHLY_PANDI',
   'SCHEDULED_MONTHLY_PANDI_NAN', 
   'LLMA2_CURRENT_INTEREST_SPREAD', 'LLMA2_CURRENT_INTEREST_SPREAD_NAN',  
   'LLMA2_C_IN_LAST_12_MONTHS',
   'LLMA2_30_IN_LAST_12_MONTHS', 'LLMA2_60_IN_LAST_12_MONTHS',
   'LLMA2_90_IN_LAST_12_MONTHS', 'LLMA2_FC_IN_LAST_12_MONTHS',
   'LLMA2_REO_IN_LAST_12_MONTHS', 'LLMA2_0_IN_LAST_12_MONTHS',       
   'NUM_MODIF', 'NUM_MODIF_NAN', 'P_RATE_TO_MOD', 'P_RATE_TO_MOD_NAN', 'MOD_RATE',
   'MOD_RATE_NAN', 'DIF_RATE', 'DIF_RATE_NAN', 'P_MONTHLY_PAY',
   'P_MONTHLY_PAY_NAN', 'MOD_MONTHLY_PAY', 'MOD_MONTHLY_PAY_NAN',
   'DIF_MONTHLY_PAY', 'DIF_MONTHLY_PAY_NAN', 'CAPITALIZATION_AMT',
   'CAPITALIZATION_AMT_NAN', 'MORTGAGE_RATE', 'MORTGAGE_RATE_NAN',
   'FICO_SCORE_ORIGINATION', 'INITIAL_INTEREST_RATE', 'ORIGINAL_LTV',
   'ORIGINAL_BALANCE', 'BACKEND_RATIO', 'BACKEND_RATIO_NAN',
   'ORIGINAL_TERM', 'ORIGINAL_TERM_NAN', 'SALE_PRICE', 'SALE_PRICE_NAN', 	   
   'PREPAY_PENALTY_TERM', 'PREPAY_PENALTY_TERM_NAN', 
    'NUMBER_OF_UNITS', 'NUMBER_OF_UNITS_NAN', 'MARGIN',
   'MARGIN_NAN', 'PERIODIC_RATE_CAP', 'PERIODIC_RATE_CAP_NAN',
   'PERIODIC_RATE_FLOOR', 'PERIODIC_RATE_FLOOR_NAN', 'LIFETIME_RATE_CAP',
   'LIFETIME_RATE_CAP_NAN', 'LIFETIME_RATE_FLOOR',
   'LIFETIME_RATE_FLOOR_NAN', 'RATE_RESET_FREQUENCY',
   'RATE_RESET_FREQUENCY_NAN', 'PAY_RESET_FREQUENCY',
   'PAY_RESET_FREQUENCY_NAN', 'FIRST_RATE_RESET_PERIOD',
   'FIRST_RATE_RESET_PERIOD_NAN', 	           
   'LLMA2_ORIG_RATE_SPREAD', 'LLMA2_ORIG_RATE_SPREAD_NAN', 
   'AGI', 'AGI_NAN', 'UR', 'UR_NAN', 'LLMA2_ORIG_RATE_ORIG_MR_SPREAD', 
   'LLMA2_ORIG_RATE_ORIG_MR_SPREAD_NAN', 'NUM_PRIME_ZIP', 'NUM_PRIME_ZIP_NAN'
   ]

ncols = [x for x in numeric_cols if x.find('NAN')<0]

print(ncols)

In [ ]:
#mixing with NAN values:
ncols_idxs = [i for i, x in enumerate(df_sample_scat.columns.values) if x in ncols]
print(len(ncols_idxs), ncols_idxs)

In [ ]:
# unique values and removing the unique values with an unique value:
for column in df_sample_scat:
    if len(df_sample_scat[column].unique()) <=1:
        print(column, df_sample_scat[column].unique())

In [ ]:
cat_idxs = [i for i in list(range(101)) if i not in ncols_idxs]
print(len(cat_idxs), cat_idxs)

In [ ]:
cat_names = [x for i, x in enumerate(df_sample_scat.columns.values) if x not in ncols]
print(len(cat_names), cat_names)

In [ ]:
#statistics for categorical columns:
for column in cat_names: 
    display(df_sample_scat[column].value_counts())
    display(df_sample_scat[column].astype('category').describe())

In [ ]:
#statistics for numerical columns:
for column in ncols: 
    display(df_sample_scat[column].value_counts())
    display(df_sample_scat[column].describe())

In [ ]:
clusters = kp.fit(df_sample_scat.values, categorical=cat_idxs)

In [ ]:
clusters = kp.predict(df_sample_scat.values, categorical=cat_idxs)

In [ ]:
# Print the cluster centroids
print('cluster centroids numerical features: ', kp.cluster_centroids_[0].shape, kp.cluster_centroids_[0])
print('cluster centroids categorical features: ', kp.cluster_centroids_[1].shape, kp.cluster_centroids_[1])
clt_cent = [np.append(i, j) for i, j in zip(kp.cluster_centroids_[0], kp.cluster_centroids_[1])]
clt_cent = np.array(clt_cent)
print(clt_cent.shape, clt_cent)

In [ ]:
np.savetxt("kprototypes_Centroids_C_C.csv", clt_cent, delimiter=";")

In [ ]:
print(len(clusters), clusters)
print('Cluster Summary %s' % Counter(clusters))

In [ ]:
#df_sample_scat['MBA_DELINQUENCY_STATUS']

In [ ]:
clusters = pd.Series(clusters)

In [ ]:
#clusters.hist()

In [ ]:
clusters.value_counts().plot(kind="bar") #

In [ ]:
import kmodes.kprototypes as kpt

#, categorical=cat_idxs


#Xnum = np.asanyarray(X[:, [ii for ii in range(X.shape[1])
#                               if ii not in categorical]]).astype(np.float64)
#Xcat = np.asanyarray(X[:, categorical])


Xnum, Xcat = kpt._split_num_cat(df_sample_scat.values, cat_idxs)
Xnum, Xcat = kpt.check_array(Xnum), kpt.check_array(Xcat, dtype=None)
Xcat, _ = kpt.encode_features(Xcat, enc_map=kp._enc_map)
    

In [ ]:
print(Xnum.shape, Xnum)
print(Xcat.shape, Xcat)

In [ ]:
distances = np.empty((n_points,kp.n_clusters), dtype=np.float32)
distances.shape

In [ ]:
n_points = Xnum.shape[0]
labels = np.empty(n_points, dtype=np.uint16)
distances = np.empty((n_points,kp.n_clusters), dtype=np.float32)
for ipoint in range(n_points):
    num_costs = kp.num_dissim(kp.cluster_centroids_[0], Xnum[ipoint])
    cat_costs = kp.cat_dissim(kp.cluster_centroids_[1], Xcat[ipoint], X=Xcat)
    # Gamma relates the categorical cost to the numerical cost.
    tot_costs = num_costs + kp.gamma * cat_costs    
    clust = np.argmin(tot_costs)
    labels[ipoint] = clust
    distances[ipoint, :] = tot_costs

In [ ]:
print(len(labels), labels)
print(distances.shape, distances)

In [ ]:
print((labels == clusters.values).all())

In [ ]:
#carat_table = pd.crosstab(index=clusters.values, columns=y_sample.values)

In [ ]:
#print(clusters)
#print(y_sample)

In [ ]:
#class_dict = {'0': 0, '3': 1, '6': 2, '9': 3, 'C': 4, 'F': 5, 'R': 6}
#carat_table.index = ['Cluster_'+str(i) for i in sorted(clusters.value_counts().index.values)]
#carat_table.columns = ['Class_'+ elem for elem in class_dict.keys()]

#print(carat_table)
#print(carat_table.sum().sum())

In [ ]:
#my_plot = carat_table.plot(kind="bar", figsize=(15,8),stacked=True)
##rot = 70 if (len(col_index.unique()) >= 10) else 0     
#my_plot.set_xticklabels(carat_table.index, rotation=0)    
##my_plot.set_xlabel('')
#my_plot.get_figure().savefig("kprototypes_Clusters_Classes.png")

In [ ]:
##plt.show()
##plt.close()
##plt.clf()
print(len(kp.labels_), kp.labels_)
print(kp.gamma)
#print(df_sample_scat.values.shape)

In [ ]:
for c, ds, values in zip(clusters.values, distances, df_sample_scat.values):
    arr = np.append(np.append(float(c), np.array(ds)), values)
    print(arr)

In [ ]:
print(arr.shape)

In [ ]:
neighborhood = [np.append(np.append(float(c), np.array(ds)), values) for c, ds, values in zip(clusters.values, distances, df_sample_scat.values)]
neighborhood = np.array(neighborhood)
print(neighborhood.shape, neighborhood)

In [ ]:
np.savetxt("kprototypes_details_alld_C_C.csv", neighborhood, delimiter=";")